In [142]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

plt.style.use('ggplot')

import nltk

In [143]:
# Read in data
df = pd.read_csv('/kaggle/input/amazon-fine-food-reviews/Reviews.csv')
print(df.shape)
df = df.head(500)
print(df.shape)

(568454, 10)
(500, 10)


In [147]:
ax = df['Score'].value_counts()
ax

Score
5    339
4     70
3     37
1     36
2     18
Name: count, dtype: int64

In [148]:
#BAsic NLTK
example = df['Text'][50]
print(example)

This oatmeal is not good. Its mushy, soft, I don't like it. Quaker Oats is the way to go.


In [149]:
df.head()

Id   ProductId          UserId                      ProfileName  \
0   1  B001E4KFG0  A3SGXH7AUHU8GW                       delmartian   
1   2  B00813GRG4  A1D87F6ZCVE5NK                           dll pa   
2   3  B000LQOCH0   ABXLMWJIXXAIN  Natalia Corres "Natalia Corres"   
3   4  B000UA0QIQ  A395BORC6FGVXV                             Karl   
4   5  B006K2ZZ7K  A1UQRSCLF8GW1T    Michael D. Bigham "M. Wassir"   

   HelpfulnessNumerator  HelpfulnessDenominator  Score        Time  \
0                     1                       1      5  1303862400   
1                     0                       0      1  1346976000   
2                     1                       1      4  1219017600   
3                     3                       3      2  1307923200   
4                     0                       0      5  1350777600   

                 Summary                                               Text  
0  Good Quality Dog Food  I have bought several of the Vitality canned d...  
1      Not as Advertised  Product arrived labeled as Jumbo Salted Peanut...  
2  "Delight" says it all  This is a confection that has been around a fe...  
3         Cough Medicine  If you are looking for the secret ingredient i...  
4            Great taffy  Great taffy at a great price.  There was a wid...

In [150]:
tokens = nltk.word_tokenize(example)
tokens[:10]

['This', 'oatmeal', 'is', 'not', 'good', '.', 'Its', 'mushy', ',', 'soft']

In [151]:
nltk.download('averaged_perceptron_tagger_eng')


[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     /usr/share/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_eng is already up-to-
[nltk_data]       date!


True

In [152]:
tagged = nltk.pos_tag(tokens)
tagged[:10]

[('This', 'DT'),
 ('oatmeal', 'NN'),
 ('is', 'VBZ'),
 ('not', 'RB'),
 ('good', 'JJ'),
 ('.', '.'),
 ('Its', 'PRP$'),
 ('mushy', 'NN'),
 (',', ','),
 ('soft', 'JJ')]

In [153]:
nltk.download('maxent_ne_chunker_tab')

[nltk_data] Downloading package maxent_ne_chunker_tab to
[nltk_data]     /usr/share/nltk_data...
[nltk_data]   Package maxent_ne_chunker_tab is already up-to-date!


True

In [154]:
entities = nltk.chunk.ne_chunk(tagged)
entities.pprint()

(S
  This/DT
  oatmeal/NN
  is/VBZ
  not/RB
  good/JJ
  ./.
  Its/PRP$
  mushy/NN
  ,/,
  soft/JJ
  ,/,
  I/PRP
  do/VBP
  n't/RB
  like/VB
  it/PRP
  ./.
  (ORGANIZATION Quaker/NNP Oats/NNPS)
  is/VBZ
  the/DT
  way/NN
  to/TO
  go/VB
  ./.)


**VADER Seniment Scoring**

In [155]:
#from nltk.sentiment import SentimentIntensityAnalyzer
#from tqdm.notebook import tqdm

#sia = SentimentIntensityAnalyzer()

In [156]:
#sia.polarity_scores('I am so happy!')
#neg- Negative
#neu- neutral
#pos- Positivew

In [157]:
#sia.polarity_scores('This is the worst thing ever.')

In [158]:
#sia.polarity_scores(example)

In [159]:
# Run the polarity score on the entire dataset
#res = {}
#for i, row in tqdm(df.iterrows(), total=len(df)):
    #text = row['Text']
    #myid = row['Id']
    #res[myid] = sia.polarity_scores(text)

In [160]:
#pd.DataFrame(res)

In [161]:
#vaders = pd.DataFrame(res).T
#vaders = vaders.reset_index().rename(columns={'index': 'Id'})
#vaders = vaders.merge(df, how='left')


In [162]:
#vaders.head()

**Plot VADER results**

In [163]:
#ax = sns.barplot(data=vaders, x='Score', y='compound')
#ax.set_title('Compund Score by Amazon Star Review')
#plt.show()

In [164]:
#fig, axs = plt.subplots(1, 3, figsize=(12, 3))
#sns.barplot(data=vaders, x='Score', y='pos', ax=axs[0])
#sns.barplot(data=vaders, x='Score', y='neu', ax=axs[1])
#sns.barplot(data=vaders, x='Score', y='neg', ax=axs[2])
#axs[0].set_title('Positive')
#axs[1].set_title('Neutral')
#axs[2].set_title('Negative')
#plt.tight_layout()
#plt.show()

**Step 3. Roberta Pretrained Model**

In [165]:
from transformers import AutoTokenizer
from transformers import AutoModelForSequenceClassification
from scipy.special import softmax

In [166]:
import torch
from torch.utils.data import Dataset, DataLoader
from torch.optim import AdamW
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import pandas as pd
from tqdm import tqdm

# Model and Tokenizer
MODEL = "cardiffnlp/twitter-roberta-base-sentiment"
tokenizer = AutoTokenizer.from_pretrained(MODEL)
model = AutoModelForSequenceClassification.from_pretrained(
    MODEL,
    num_labels=2,
    ignore_mismatched_sizes=True  # ✅ Fix size mismatch
)

# Custom Dataset
class ReviewDataset(Dataset):
    def __init__(self, texts, labels, tokenizer, max_len=128):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_len = max_len

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        encoding = self.tokenizer(self.texts[idx], truncation=True, padding='max_length', max_length=self.max_len, return_tensors="pt")
        return {
            'input_ids': encoding['input_ids'].flatten(),
            'attention_mask': encoding['attention_mask'].flatten(),
            'labels': torch.tensor(self.labels[idx], dtype=torch.long)
        }

# Data prep
df = df[df['Score'].isin([1, 2, 4, 5])]
df['label'] = df['Score'].apply(lambda x: 0 if x < 3 else 1)
texts = df['Text'].fillna("").tolist()
labels = df['label'].tolist()

# Dataset and DataLoader
dataset = ReviewDataset(texts, labels, tokenizer)
dataloader = DataLoader(dataset, batch_size=8, shuffle=True)

# Setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)
optimizer = AdamW(model.parameters(), lr=2e-5)

# Training Loop (3 epochs)
model.train()
for epoch in range(3):
    total_loss = 0
    print(f"\nEpoch {epoch+1}")
    for batch in tqdm(dataloader):
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['labels'].to(device)

        outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels)
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    
    print(f"Epoch {epoch+1} Loss: {total_loss:.4f}")

# Evaluation
model.eval()
all_preds = []
all_labels = []

with torch.no_grad():
    for batch in dataloader:
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['labels'].to(device)

        outputs = model(input_ids=input_ids, attention_mask=attention_mask)
        preds = torch.argmax(outputs.logits, dim=1)

        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())

# Metrics
acc = accuracy_score(all_labels, all_preds)
prec = precision_score(all_labels, all_preds)
rec = recall_score(all_labels, all_preds)
f1 = f1_score(all_labels, all_preds)

print(f"\n✅ Evaluation Metrics:")
print(f"Accuracy:  {acc:.4f}")
print(f"Precision: {prec:.4f}")
print(f"Recall:    {rec:.4f}")
print(f"F1 Score:  {f1:.4f}")


Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment and are newly initialized because the shapes did not match:
- classifier.out_proj.weight: found shape torch.Size([3, 768]) in the checkpoint and torch.Size([2, 768]) in the model instantiated
- classifier.out_proj.bias: found shape torch.Size([3]) in the checkpoint and torch.Size([2]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.



Epoch 1


100%|██████████| 58/58 [05:03<00:00,  5.23s/it]


Epoch 1 Loss: 11.8127

Epoch 2


100%|██████████| 58/58 [04:50<00:00,  5.02s/it]


Epoch 2 Loss: 5.3162

Epoch 3


100%|██████████| 58/58 [04:58<00:00,  5.14s/it]


Epoch 3 Loss: 4.4434

✅ Evaluation Metrics:
Accuracy:  0.9719
Precision: 0.9692
Recall:    1.0000
F1 Score:  0.9844


In [193]:
model.save_pretrained('finetuned-model')
tokenizer.save_pretrained('finetuned-model')

('finetuned-model/tokenizer_config.json',
 'finetuned-model/special_tokens_map.json',
 'finetuned-model/vocab.json',
 'finetuned-model/merges.txt',
 'finetuned-model/added_tokens.json',
 'finetuned-model/tokenizer.json')

In [168]:
MODEL = f"cardiffnlp/twitter-roberta-base-sentiment"
tokenizer = AutoTokenizer.from_pretrained(MODEL)
model = AutoModelForSequenceClassification.from_pretrained(MODEL)

In [169]:
# Run for Roberta Model
encoded_text = tokenizer(example, return_tensors='pt')
output = model(**encoded_text)
scores = output[0][0].detach().numpy()
scores = softmax(scores)
scores_dict = {
    'roberta_neg' : scores[0],
    'roberta_neu' : scores[1],
    'roberta_pos' : scores[2]
}
print(scores_dict)

{'roberta_neg': 0.97635514, 'roberta_neu': 0.020687463, 'roberta_pos': 0.0029573694}


In [170]:
def polarity_scores_roberta(example):
    encoded_text = tokenizer(example, return_tensors='pt')
    output = model(**encoded_text)
    scores = output[0][0].detach().numpy()
    scores = softmax(scores)
    scores_dict = {
        'roberta_neg' : scores[0],
        'roberta_neu' : scores[1],
        'roberta_pos' : scores[2]
    }
    return scores_dict

In [171]:
res = {}
for i, row in tqdm(df.iterrows(), total=len(df)):
    try:
        text = row['Text']
        myid = row['Id']
        vader_result = sia.polarity_scores(text)
        vader_result_rename = {}
        for key, value in vader_result.items():
            vader_result_rename[f"vader_{key}"] = value
        roberta_result = polarity_scores_roberta(text)
        both = {**vader_result_rename, **roberta_result}
        res[myid] = both
    except RuntimeError:
        print(f'Broke for id {myid}')

 17%|█▋        | 77/463 [00:13<00:44,  8.73it/s]

Broke for id 83


 37%|███▋      | 172/463 [00:29<00:28, 10.09it/s]

Broke for id 187


100%|██████████| 463/463 [01:20<00:00,  5.78it/s]


In [172]:
results_df = pd.DataFrame(res).T
results_df = results_df.reset_index().rename(columns={'index': 'Id'})
results_df = results_df.merge(df, how='left')

In [173]:
from sklearn.metrics import precision_score,recall_score,f1_score

In [174]:
results_df

Id  vader_neg  vader_neu  vader_pos  vader_compound  roberta_neg  \
0      1      0.000      0.695      0.305          0.9441     0.009624   
1      2      0.138      0.862      0.000         -0.5664     0.508986   
2      3      0.091      0.754      0.155          0.8265     0.003229   
3      4      0.000      1.000      0.000          0.0000     0.002295   
4      5      0.000      0.552      0.448          0.9468     0.001635   
..   ...        ...        ...        ...             ...          ...   
456  496      0.000      0.554      0.446          0.9725     0.001906   
457  497      0.059      0.799      0.142          0.7833     0.004415   
458  498      0.025      0.762      0.212          0.9848     0.006427   
459  499      0.041      0.904      0.055          0.1280     0.865614   
460  500      0.000      0.678      0.322          0.9811     0.002440   

     roberta_neu  roberta_pos   ProductId          UserId  \
0       0.049980     0.940395  B001E4KFG0  A3SGXH7AUHU8GW   
1       0.452414     0.038600  B00813GRG4  A1D87F6ZCVE5NK   
2       0.098067     0.898704  B000LQOCH0   ABXLMWJIXXAIN   
3       0.090219     0.907486  B000UA0QIQ  A395BORC6FGVXV   
4       0.010302     0.988063  B006K2ZZ7K  A1UQRSCLF8GW1T   
..           ...          ...         ...             ...   
456     0.009862     0.988232  B000G6RYNE   APGAA43E3WPN7   
457     0.034215     0.961369  B000G6RYNE    ABR7HU5H1KNE   
458     0.074537     0.919036  B000G6RYNE   AJQD2WWJYOYFQ   
459     0.119366     0.015020  B000G6RYNE  A16YH487W9ZYO0   
460     0.011327     0.986233  B000G6RYNE   A83YQC1XOU4CS   

                         ProfileName  HelpfulnessNumerator  \
0                         delmartian                     1   
1                             dll pa                     0   
2    Natalia Corres "Natalia Corres"                     1   
3                               Karl                     3   
4      Michael D. Bigham "M. Wassir"                     0   
..                               ...                   ...   
456                           Darren                     0   
457                            Keith                     0   
458                          bubbles                     0   
459                 Bruce G. Lindsay                     0   
460                         J. Baker                     0   

     HelpfulnessDenominator  Score        Time  \
0                         1      5  1303862400   
1                         0      1  1346976000   
2                         1      4  1219017600   
3                         3      2  1307923200   
4                         0      5  1350777600   
..                      ...    ...         ...   
456                       0      5  1201392000   
457                       0      5  1196726400   
458                       0      4  1186617600   
459                       0      4  1184198400   
460                       0      5  1183420800   

                             Summary  \
0              Good Quality Dog Food   
1                  Not as Advertised   
2              "Delight" says it all   
3                     Cough Medicine   
4                        Great taffy   
..                               ...   
456                    amazing chips   
457                   Best Chip Ever   
458  Tangy, spicy, and sweet- oh my!   
459        An indulgence with a bite   
460                The best I've had   

                                                  Text  label  
0    I have bought several of the Vitality canned d...      1  
1    Product arrived labeled as Jumbo Salted Peanut...      0  
2    This is a confection that has been around a fe...      1  
3    If you are looking for the secret ingredient i...      0  
4    Great taffy at a great price.  There was a wid...      1  
..                                                 ...    ...  
456  i rarely eat chips but i saw these and tried t...      1  
457  This is easily the best potato chip that

In [175]:
results_df.columns

Index(['Id', 'vader_neg', 'vader_neu', 'vader_pos', 'vader_compound',
       'roberta_neg', 'roberta_neu', 'roberta_pos', 'ProductId', 'UserId',
       'ProfileName', 'HelpfulnessNumerator', 'HelpfulnessDenominator',
       'Score', 'Time', 'Summary', 'Text', 'label'],
      dtype='object')

In [176]:
results_df.query('Score == 1') \
    .sort_values('roberta_pos', ascending=False)['Text'].values[0]

'I felt energized within five minutes, but it lasted for about 45 minutes. I paid $3.99 for this drink. I could have just drunk a cup of coffee and saved my money.'

In [177]:
results_df.query('Score == 1') \
    .sort_values('vader_pos', ascending=False)['Text'].values[0]

'So we cancelled the order.  It was cancelled without any problem.  That is a positive note...'

In [178]:
results_df.query('Score == 5') \
    .sort_values('roberta_neg', ascending=False)['Text'].values[0]

'this was sooooo deliscious but too bad i ate em too fast and gained 2 pds! my fault'

In [179]:
results_df.query('Score == 5') \
    .sort_values('vader_neg', ascending=False)['Text'].values[0]

'this was sooooo deliscious but too bad i ate em too fast and gained 2 pds! my fault'

In [180]:
from transformers import pipeline

sent_pipeline = pipeline("sentiment-analysis")

No model was supplied, defaulted to distilbert/distilbert-base-uncased-finetuned-sst-2-english and revision 714eb0f (https://huggingface.co/distilbert/distilbert-base-uncased-finetuned-sst-2-english).
Using a pipeline without specifying a model name and revision in production is not recommended.
Device set to use cpu


In [181]:
sent_pipeline('I Love sentiment analysis!')

[{'label': 'POSITIVE', 'score': 0.9997853636741638}]

In [182]:
sent_pipeline('I hate sentiment analysis!')

[{'label': 'NEGATIVE', 'score': 0.9992958307266235}]

In [183]:
sent_pipeline('Make sure to like and subscribe!')

[{'label': 'POSITIVE', 'score': 0.9991742968559265}]

In [185]:
sent_pipeline('Make sure to not like and subscribe!')

[{'label': 'NEGATIVE', 'score': 0.8641592264175415}]

In [186]:
sent_pipeline('booo')

[{'label': 'NEGATIVE', 'score': 0.9936267137527466}]

In [187]:
sent_pipeline('good')

[{'label': 'POSITIVE', 'score': 0.9998161196708679}]

In [188]:
sent_pipeline('bad')

[{'label': 'NEGATIVE', 'score': 0.999782383441925}]

In [190]:
sent_pipeline('i like it')

[{'label': 'POSITIVE', 'score': 0.9998593330383301}]

In [191]:
quantized_model = torch.quantization.quantize_dynamic(
    model, {torch.nn.Linear}, dtype=torch.qint8
)
print("Quantized model ready")

Quantized model ready


In [192]:
torch.save(quantized_model.state_dict(), "sentient_model.pt")

In [205]:
finetuned_model = AutoModelForSequenceClassification.from_pretrained('/kaggle/working/finetuned-model')
tokenizer = AutoTokenizer.from_pretrained('/kaggle/working/finetuned-model')

In [206]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [207]:
quantize_model = finetuned_model.to(dtype=torch.float16, device=device)

In [209]:
quantize_model.save_pretrained('quantized-model')
tokenizer.save_pretrained('quantized-model')

('quantized-model/tokenizer_config.json',
 'quantized-model/special_tokens_map.json',
 'quantized-model/vocab.json',
 'quantized-model/merges.txt',
 'quantized-model/added_tokens.json',
 'quantized-model/tokenizer.json')

In [212]:
import torch.nn.functional as F

In [ ]:
# Predict
def predict(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=128)
    with torch.no_grad():
        outputs = quantize_model(**inputs)
        probs = F.softmax(outputs.logits, dim=1)
        pred = torch.argmax(probs, dim=1).item()
        label_map = {0: "Negative", 1: "Neutral", 2: "Positive"}
    return f"Sentiment: {label_map[pred]} (Confidence: {probs[0][pred]:.2f})"

In [ ]:
# Test predictions
print("\nTest Predictions:")
print(predict("the product quality is just so so"))